# Úkol: BI-PST


Spolupracovali:
   * Ondřej Hladůvka (reprezentant)
   * Tomáš Kaňka

In [ ]:
#import csv
#import math
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
#np.set_printoptions(precision=3)
#from sympy import *
from scipy import stats 
from scipy.stats import norm, uniform, expon
#from scipy.optimize import minimize

In [ ]:
K = 28
L = 8
M = (((K + L) * 47) % 11) + 1
print(M)

## Úloha č. 1

(1b) Načtěte datový soubor a rozdělte sledovanou proměnnou na příslušné dvě pozorované skupiny.
Stručně popište data a zkoumaný problém. Pro každou skupinu zvlášť odhadněte střední hodnotu, rozptyl a medián příslušného rozdělení.

In [ ]:
# načtení dat
df = pd.read_csv("/data.csv")
df = df.drop(df.columns[0], axis=1)
survived = df[df['Status'] == 'survived']['Weight'].values
perished = df[df['Status'] == 'perished']['Weight'].values
# informace
print("Prvních 5 řádků:")
print(df.head())
print("Info")
print("Počet řádků:", df.shape[0])
print("Datové typy:")
display(df.info())


Tento datový soubor zkoumá, zda hmotnost dospělých samců vrabců hraje roli v jejich přežití během extrémních klimatických podmínek. Cílem je zjistit, zda vrabci, kteří přežili, měli významně jinou průměrnou hmotnost ve srovnání se vrabci, kteří zahynuli. 

Tabulak má dva sloupce weight a status, kde
**weight** udává hmotnost dospělých samců vrabců v gramech a
**status**  udává, zda vrabec přežil nebo zahynul během zimní bouře. Může mít hodnoty "survived" (přežil) nebo "perished" (zahynul).


In [ ]:
# Zobrazení názvů sloupců
print(df.columns)

groups = df.groupby('Status')
summary_stats = groups['Weight'].agg(['mean', 'var', 'median']).reset_index()

# Zobrazení výsledků
print(summary_stats)

## Úloha č. 2

(1b) Pro každou skupinu zvlášť odhadněte hustotu a distribuční funkci pomocí histogramu a empirické distribuční funkce.

In [ ]:
# Funkce pro výpočet hustoty a CDF
def calculate_density_cdf(group):
    sorted_weights = group.sort_values('Weight')
    
    # Výpočet CDF
    cdf = pd.Series(range(1, len(sorted_weights) + 1)) / len(sorted_weights)
    
    # Přidání CDF k seřazeným váhám
    results = pd.DataFrame({'Weight': sorted_weights['Weight'].values, 'CDF': cdf.values})
    
    return results

# Vytvoření hustoty a CDF pro každou skupinu
groups = df.groupby('Status')
density_cdf_results = {}

for name, group in groups:
    density_cdf_results[name] = calculate_density_cdf(group)

# Zobrazení výsledků
for name, results in density_cdf_results.items():
    plt.figure(figsize=(10, 6))
    plt.hist(df[df['Status'] == name]['Weight'], bins=20, density=True, alpha=0.5, label=f'Hustota {name}')
    
    # CDF
    plt.plot(results['Weight'], results['CDF'], label=f'CDF {name}', color='red')
    
    # Nastavení g
    plt.title(f'Hustota a CDF pro skupinu: {name}')
    plt.xlabel('Hmotnost')
    plt.ylabel('Hustota / Kumulativní pravděpodobnost (CDF)')
    plt.legend()
    plt.grid()
    plt.show()
    print(f"\n--- Výsledky pro skupinu: {name} ---")
    print(results)




Vytvořili jsme funkci calculate_density_cdf, která seřadila data podle hmotnosti a spočítala kumulativní distribuční funkci. Tato funkce vrátila DataFrame se seřazenými hmotnostmi a odpovídajícími hodnotami CDF.

## Úloha č. 3

(3b) Pro každou skupinu zvlášť najděte nejbližší rozdělení: 
Odhadněte parametry normálního, exponenciálního a rovnoměrného rozdělení.
Zaneste příslušné hustoty s odhadnutými parametry do grafů histogramu. Diskutujte, které z rozdělení odpovídá pozorovaným datům nejlépe.

In [ ]:
def show_distribution(data):
    fig = plt.figure(figsize = (10, 14))
    gs = fig.add_gridspec(4,2, figure = fig)
    sp1 = fig.add_subplot(gs[0, 0])
    sp2 = fig.add_subplot(gs[0, 1])
    sp3 = fig.add_subplot(gs[1, 0])
    sp4 = fig.add_subplot(gs[1, 1])
    sp5 = fig.add_subplot(gs[ 2:, 0:])
    
    sp1.set_title('Data Histogram')
    sp1.hist(data, bins=10, density=True, alpha=0.5)
    sp2.hist(data, bins=10, density=True, alpha=0.5)
    sp3.hist(data, bins=10, density=True, alpha=0.5)
    sp4.hist(data, bins=10, density=True, alpha=0.5)
    sp5.hist(data, bins=10, density=True, alpha=0.5)
    
    mu, std = norm.fit(data)  # Get mean and standard deviation
    xmin, xmax = sp1.get_xlim()  # Get x-axis limits from the histogram
    x = np.linspace(xmin, xmax, 100)
    p_norm = norm.pdf(x, mu, std)  # Generate the PDF for the normal distribution
    sp2.plot(x, p_norm, 'red')
    sp2.fill_between(x, p_norm, alpha=0.2, color='red')
    sp2.set_title(f'Normal fit ($\mu={mu:.2f}, \sigma={std:.2f}$)')

    loc, scale = expon.fit(data)
    p_exp = expon.pdf(x, loc, scale)
    split0 = next((i for i, x in enumerate(p_exp) if x != 0), len(p_exp))
    sp3.plot(x[split0:], p_exp[split0:], 'green')
    sp3.fill_between(x[split0:], p_exp[split0:], alpha=0.2, color='green')
    sp3.set_title(f'Exponential Distribution Fit (scale={scale:.2f})')

    loc_uni, scale_uni = uniform.fit(data)
    p_uni = uniform.pdf(x, loc_uni, scale_uni)
    split1 = next((i for i, x in enumerate(p_uni) if x != 0), len(p_uni))
    split2 = -next((i for i, x in enumerate(reversed(p_uni)) if x != 0), len(p_uni))
    sp4.plot(x[split1:split2], p_uni[split1:split2], 'purple')
    sp4.plot(x[:split1], p_uni[:split1], 'purple')
    sp4.plot(x[split2:], p_uni[split2:], 'purple')
    sp4.fill_between(x[split1:split2], p_uni[split1:split2], alpha=0.1, color='purple')
    sp4.set_title(f'Uniform Distribution Fit (range=({loc_uni:.2f}, {loc_uni+scale_uni:.2f}))')
     
    sp5.plot(x, p_norm, 'red', label=f'Normal fit: $\mu={mu:.2f}, \sigma={std:.2f}$')
    sp5.plot(x[split0:], p_exp[split0:], 'green', label=f'Exponential fit: scale={scale:.2f}')
    sp5.plot(x[split1:split2], p_uni[split1:split2], 'purple')
    sp5.plot(x[:split1], p_uni[:split1], 'purple')
    sp5.plot(x[split2:], p_uni[split2:], 'purple', label=f'Uniform fit: range=({loc_uni:.2f}, {loc_uni+scale_uni:.2f})')
    #sp5.plot(x, p_uni, 'blue', label=f'Uniform fit: range=({loc_uni:.2f}, {loc_uni+scale_uni:.2f})')
    sp5.set_title('Combined Distributions')
    sp5.legend()

In [ ]:
show_distribution(survived)
show_distribution(perished)

## Úloha č. 4

(1b) Pro každou skupinu zvlášť vygenerujte náhodný výběr o 100 hodnotách z rozdělení, 
které jste zvolili jako nejbližší, s parametry odhadnutými v předchozím bodě.
Porovnejte histogram simulovaných hodnot s pozorovanými daty.

In [ ]:
def showRandomData(mean, std, dataset, title):
    data = np.random.normal(mean, std, 100)
    plt.figure(figsize=(10, 6))
    x = np.linspace(data.min() - 5, data.max() + 5, 100)
    p_norm = norm.pdf(x, mean, std)
    plt.plot(x, p_norm, 'black', linewidth = 2)
    plt.hist(data, bins = 10, color = "blue", alpha=0.5 , density = True)
    #plt.set_title("Náhodné hodnoty z normálního rozdělení")
    plt.hist(dataset, bins = 10, color = "green", alpha=0.5, density = True)
    plt.show()

In [ ]:
mean_survived, std_survived = norm.fit(survived)
showRandomData(mean_survived, std_survived, survived, "survived")
mean_perished, std_perished = norm.fit(perished)
showRandomData(mean_perished, std_perished, survived, "perished")

## Úloha č. 5

(1b) Pro každou skupinu zvlášť spočítejte oboustranný 95% konfidenční interval pro střední hodnotu.

In [ ]:
def conf_interval(data, name):
    conf = stats.t.interval(confidence = 0.95, df = len(data) - 1, loc = np.mean(data), scale = stats.sem(data))
    print(f"Oboustranný konfidenční interval 95% střední hodnoty skupiny \"{name}\":", conf)
    return conf

In [ ]:
def plot_conf_interval(title, list, interval):
    fig, ax = plt.subplots(figsize = (6, 4))
    ax.hist(list, bins = 10, color = "royalblue", edgecolor = "black")
    ax.set_title(f"Oboustranný 95% interval pro skupinu \"{title}\"")
    ax.axvline(x = interval[0], color = "red")
    ax.axvline(x = interval[1], color = "red")
    plt.show()

In [ ]:
conf_survived = conf_interval(survived, "survived")
conf_perished = conf_interval(perished, "perished")

In [ ]:
plot_conf_interval("survived", survived, conf_survived)
plot_conf_interval("perished", perished, conf_perished)

## Úloha č. 6

(1b) Pro každou skupinu zvlášť otestujte na hladině významnosti 5 % hypotézu,
zda je střední hodnota rovná hodnotě K (parametr úlohy), proti oboustranné alternativě.
Můžete použít buď výsledek z předešlého bodu, nebo výstup z příslušné vestavěné funkce vašeho softwaru.

## Úloha č. 7

(2b) Na hladině významnosti 5 % otestujte, jestli mají pozorované skupiny stejnou střední hodnotu.
Typ testu a alternativy stanovte tak, aby vaše volba nejlépe korespondovala s povahou zkoumaného problému.